# Collect data comment Youtube Rewind Indonesia 2018 dengan Google Client API

Import library

In [1]:
from dotenv import load_dotenv
import os
import googleapiclient.discovery
import pandas as pd
from pymongo import MongoClient

Mengakses value dari file env

In [2]:
# Memuat value dari file .env
load_dotenv()

dev = os.getenv('API_KEY_1')
mongodb_url = os.getenv('URL_SANDY')
local_url = os.getenv('URL_LOCAL')

Inisialisasi videoID dan database name

In [3]:
video_id = "mCyITaDib7M"
database_name = "youtube_rewind_indonesia"
collection_name = "collect_2018"

Proses collect data

In [4]:
# Konfigurasi nama layanan API dan versi yang akan digunakan
api_service_name = "youtube"
api_version = "v3"

DEVELOPER_KEY = dev

# Koneksi ke MongoDB
client = MongoClient(local_url)
db = client[database_name]
collection = db[collection_name]

# Membangun objek YouTube API dengan menggunakan kunci pengembang dan versi API yang ditentukan
youtube = googleapiclient.discovery.build(
    api_service_name, api_version, developerKey=DEVELOPER_KEY)

# Membuat permintaan (request) untuk mendapatkan data komentar dari video tertentu
request = youtube.commentThreads().list(
    part="snippet",
    videoId=video_id,  # ID video yang akan diambil komentarnya
    maxResults=100  # Jumlah maksimum komentar yang akan diambil
)

# Inisialisasi list kosong untuk menyimpan komentar
comments = []

# Mengirimkan permintaan dan mendapatkan respons
response = request.execute()

counter = 1

# Mendapatkan komentar dari respons
for item in response['items']:
    comment = item['snippet']['topLevelComment']['snippet']
    public = item['snippet']['isPublic']
    # Menambahkan semua atribut komentar ke dalam list comments dalam bentuk dictionary
    comments.append({
        'authorDisplayName': comment['authorDisplayName'], # Nama penulis komentar
        'authorProfileImageUrl': comment['authorProfileImageUrl'], # URL gambar profil penulis
        'authorChannelUrl': comment['authorChannelUrl'], # URL channel penulis
        'channelId': comment['channelId'], # ID channel penulis
        'publishedAt': comment['publishedAt'], # Waktu publikasi komentar
        'updatedAt': comment['updatedAt'], # Waktu update komentar
        'likeCount': comment['likeCount'], # Jumlah suka komentar
        'textDisplay': comment['textDisplay'], # Isi komentar yang diformat dengan tautan dan emoji yang diproses
        'textOriginal': comment['textOriginal'], # Isi komentar
        'viewerRating': comment['viewerRating'], # Rating yang diberikan oleh pengguna
        'isPublic': public # Status publikasi komentar
    })

    # Menyisipkan data ke MongoDB
    collection.insert_one(comment)
    print(f"{counter} : {comment['textOriginal']}")
    counter+=1

# Melakukan iterasi untuk mengambil komentar dari halaman berikutnya jika ada
while (1 == 1):
    try:
        nextPageToken = response['nextPageToken']  # Mengambil token untuk halaman berikutnya
    except KeyError:
        break  # Keluar dari loop jika tidak ada halaman berikutnya
    
    nextPageToken = response['nextPageToken']  # Mengambil token untuk halaman berikutnya
    
    # Membuat permintaan baru dengan menggunakan token halaman berikutnya
    nextRequest = youtube.commentThreads().list(
        part="snippet", 
        videoId=video_id,  # ID video (opsional jika tetap sama dengan sebelumnya)
        maxResults=100,  # Jumlah maksimum komentar per halaman
        pageToken=nextPageToken  # Token untuk halaman berikutnya
    )
    # Mengirimkan permintaan baru dan mendapatkan respons
    response = nextRequest.execute()

    # Mendapatkan komentar dari respons dan menambahkannya ke dalam list comments
    for item in response['items']:
        comment = item['snippet']['topLevelComment']['snippet']
        public = item['snippet']['isPublic']
        # Menambahkan semua atribut komentar ke dalam list comments dalam bentuk dictionary
        comments.append({
            'authorDisplayName': comment['authorDisplayName'], # Nama penulis komentar
            'authorProfileImageUrl': comment['authorProfileImageUrl'], # URL gambar profil penulis
            'authorChannelUrl': comment['authorChannelUrl'], # URL channel penulis
            'channelId': comment['channelId'], # ID channel penulis
            'publishedAt': comment['publishedAt'], # Waktu publikasi komentar
            'updatedAt': comment['updatedAt'], # Waktu update komentar
            'likeCount': comment['likeCount'], # Jumlah suka komentar
            'textDisplay': comment['textDisplay'], # Isi komentar yang diformat dengan tautan dan emoji yang diproses
            'textOriginal': comment['textOriginal'], # Isi komentar
            'viewerRating': comment['viewerRating'], # Rating yang diberikan oleh pengguna
            'isPublic': public # Status publikasi komentar
        })
        
        # Menyisipkan data ke MongoDB
        collection.insert_one(comment)
        print(f"{counter} : {comment['textOriginal']}")
        counter+=1

1 : Hellow
2 : Kangenn Dehh.. 🥶😭
3 : Dari 2024 😄
4 : Baru nonton di tahun 2024
5 : 2018 ternyata 6th lalu
6 : Era sebelum tiktoker menyerang
7 : Kangen youtube rewind yg dimana dulu yg masuk rewind cuma youtuber
8 : Ada kah yang menoton ini di 2024 untuk nostalgia?
9 : Tiba-tiba jadi kangen sama tahun-tahun dimana Banyak sekali drama yang terjadi dari para Youtuber 😂✌
10 : B ajah
11 : 9:10
12 : P
13 : Hallo, 2024 kangen lihat karya ericko lim hehe
14 : Oh gw inget ,video ini gw kiat pake hp pertama gw dulu😅 kangen banget asli
15 : Sebelum korona menyerang, sebelum hidup gw berantakan🥲
16 : 2024?
17 : Damn'i ep te goin saiko lel mama bad lek maikel
Cen ruly trust nobody.. With al this juwly on yu
My roof luklek ano show, got.. 
Daimons bay the boo lood
18 : masi kreatif yang ini daripada yang sekarang
19 : Dulu bnyk bahagianya ya, mulai 2020 same saat ini lebih bnyk Sedih ny T____T  Indonesia sedih,aku jg sedih,org tua udh ga ada,2018 msh ada
20 : dari segi teknis jelek semua ini rewind

In [5]:
# Membuat DataFrame dari list comments dengan kolom-kolom yang ditentukan
df = pd.DataFrame(comments)
# Menampilkan informasi DataFrame seperti jumlah baris dan tipe data kolom
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 111464 entries, 0 to 111463
Data columns (total 11 columns):
 #   Column                 Non-Null Count   Dtype 
---  ------                 --------------   ----- 
 0   authorDisplayName      111464 non-null  object
 1   authorProfileImageUrl  111464 non-null  object
 2   authorChannelUrl       111464 non-null  object
 3   channelId              111464 non-null  object
 4   publishedAt            111464 non-null  object
 5   updatedAt              111464 non-null  object
 6   likeCount              111464 non-null  int64 
 7   textDisplay            111464 non-null  object
 8   textOriginal           111464 non-null  object
 9   viewerRating           111464 non-null  object
 10  isPublic               111464 non-null  bool  
dtypes: bool(1), int64(1), object(9)
memory usage: 8.6+ MB


In [6]:
df

authorDisplayName                              authorProfileImageUrl  \
0          @azkaranuri6676  https://yt3.ggpht.com/A0rqQbMrRkVy7KLsE6h9tf0_...   
1          @BLUEBERRY_ICE.  https://yt3.ggpht.com/hJaeCYyM3zkG27NAwy7ns5LT...   
2            @Justkhanza__  https://yt3.ggpht.com/6SUOHpxm8zO3JNtlcQRN0VHv...   
3          @aryafajrin4802  https://yt3.ggpht.com/ytc/AIdro_lzu5d-GRupA7fc...   
4                  @clyzea  https://yt3.ggpht.com/e7d9_hgTBHJoCEpP_WgnB-SH...   
...                    ...                                                ...   
111459     @erlanggasp5492  https://yt3.ggpht.com/ytc/AIdro_kPkXrD0JhY2huK...   
111460          @rianr7336  https://yt3.ggpht.com/ytc/AIdro_lDYfVzt_oCeQFG...   
111461          @nick.8697  https://yt3.ggpht.com/RrBhVBns4BCdpe785raxfCtM...   
111462  @azaryapranata1108  https://yt3.ggpht.com/ytc/AIdro_k_cCFPZI6jfrqr...   
111463    @mishaeljehoshua  https://yt3.ggpht.com/ppU9UKoTkEeWvS_8JSPAindV...   

                                 authorChannelUrl                 channelId  \
0          http://www.youtube.com/@azkaranuri6676  UC-z1ubmS-iHMVr83EEwRS2g   
1          http://www.youtube.com/@BLUEBERRY_ICE.  UC-z1ubmS-iHMVr83EEwRS2g   
2            http://www.youtube.com/@Justkhanza__  UC-z1ubmS-iHMVr83EEwRS2g   
3          http://www.youtube.com/@aryafajrin4802  UC-z1ubmS-iHMVr83EEwRS2g   
4                  http://www.youtube.com/@clyzea  UC-z1ubmS-iHMVr83EEwRS2g   
...                                           ...                       ...   
111459     http://www.youtube.com/@erlanggasp5492  UC-z1ubmS-iHMVr83EEwRS2g   
111460          http://www.youtube.com/@rianr7336  UC-z1ubmS-iHMVr83EEwRS2g   
111461          http://www.youtube.com/@nick.8697  UC-z1ubmS-iHMVr83EEwRS2g   
111462  http://www.youtube.com/@azaryapranata1108  UC-z1ubmS-iHMVr83EEwRS2g   
111463    http://www.youtube.com/@mishaeljehoshua  UC-z1ubmS-iHMVr83EEwRS2g   

                 publishedAt             updatedAt  likeCount  \
0       2024-05-19T14:29:29Z  2024-05-19T14:29:29Z          1   
1       2024-05-14T19:30:18Z  2024-05-14T19:30:18Z          1   
2       2024-05-13T04:57:26Z  2024-05-13T04:57:26Z          1   
3       2024-05-10T04:30:23Z  2024-05-10T04:30:23Z          3   
4       2024-05-09T13:57:23Z  2024-05-09T13:57:23Z          2   
...                      ...                   ...        ...   
111459  2018-12-14T15:26:35Z  2018-12-14T15:27:05Z          4   
111460  2018-12-14T15:26:35Z  2018-12-14T15:26:35Z          0   
111461  2018-12-14T15:26:35Z  2018-12-14T15:26:35Z          0   
111462  2018-12-14T15:26:35Z  2018-12-14T15:26:35Z          0   
111463  2018-12-14T15:26:27Z  2018-12-14T15:26:27Z         48   

                                              textDisplay  \
0                                                  Hellow   
1                                       Kangenn Dehh.. 🥶😭   
2                                             Dari 2024 😄   
3                               Baru nonton di tahun 2024   
4                                  2018 ternyata 6th lalu   
...                                                   ...   
111459                          setelah lama menanti wkwk   
111460                                             mantap   
111461                                              Aloha   
111462                                 PINK GUY - セックス大好き   
111463  SMA SANTA MARIA-Pekanbaru selalu memberikan ya...   

                                             textOriginal viewerRating  \
0                                                  Hellow         none   
1                                       Kangenn Dehh.. 🥶😭         none   
2                                             Dari 2024 😄         none   
3                               Baru nonton di tahun 2024         none   
4                                  2018 ternyata 6th lalu         none   
...                                                   ...          ...   
111459                          setelah lama menanti wk

In [7]:
df.sort_values(by='likeCount', ascending=False)[0:10]

authorDisplayName  \
5829                 @TINATAjr   
87787      @skinnyindonesian24   
85205             @NessieJudge   
14938                   @xradt   
6340          @yakalitvesports   
20725                  @wbaaay   
29089      @wrestlingmatch6913   
83147          @kevinhendrawan   
5076   @elsaseptianisilvia5703   
3628              @kzaaa-nm9bg   

                                   authorProfileImageUrl  \
5829   https://yt3.ggpht.com/k9aA7dJNBlGJ-vPKbRqolA77...   
87787  https://yt3.ggpht.com/ytc/AIdro_lWjVa14wpop0lo...   
85205  https://yt3.ggpht.com/ytc/AIdro_mKhX_UMt80XsIz...   
14938  https://yt3.ggpht.com/TnpiHzkX93eS1rYrnULMsYCB...   
6340   https://yt3.ggpht.com/0275WzaS_rglk7dj1Po_Lgk-...   
20725  https://yt3.ggpht.com/ytc/AIdro_luXlXYtcq4HfEx...   
29089  https://yt3.ggpht.com/ytc/AIdro_kS2CdalCXXJK_W...   
83147  https://yt3.ggpht.com/IEd2vT0e6r83rtPs5UyFj6Ls...   
5076   https://yt3.ggpht.com/ytc/AIdro_nICU0YcXmbEGu2...   
3628   https://yt3.ggpht.com/ytc/AIdro_lzxTIDeMYkXz9m...   

                                     authorChannelUrl  \
5829                 http://www.youtube.com/@TINATAjr   
87787      http://www.youtube.com/@skinnyindonesian24   
85205             http://www.youtube.com/@NessieJudge   
14938                   http://www.youtube.com/@xradt   
6340          http://www.youtube.com/@yakalitvesports   
20725                  http://www.youtube.com/@wbaaay   
29089      http://www.youtube.com/@wrestlingmatch6913   
83147          http://www.youtube.com/@kevinhendrawan   
5076   http://www.youtube.com/@elsaseptianisilvia5703   
3628              http://www.youtube.com/@kzaaa-nm9bg   

                      channelId           publishedAt             updatedAt  \
5829   UC-z1ubmS-iHMVr83EEwRS2g  2020-12-28T17:12:18Z  2020-12-28T17:12:18Z   
87787  UC-z1ubmS-iHMVr83EEwRS2g  2018-12-14T16:49:04Z  2018-12-14T16:49:04Z   
85205  UC-z1ubmS-iHMVr83EEwRS2g  2018-12-14T17:13:12Z  2018-12-14T17:13:12Z   
14938  UC-z1ubmS-iHMVr83EEwRS2g  2019-06-07T16:29:20Z  2020-11-15T13:00:13Z   
6340   UC-z1ubmS-iHMVr83EEwRS2g  2020-12-24T13:06:23Z  2020-12-24T13:06:23Z   
20725  UC-z1ubmS-iHMVr83EEwRS2g  2018-12-29T14:15:45Z  2020-06-19T01:12:59Z   
29089  UC-z1ubmS-iHMVr83EEwRS2g  2018-12-18T07:44:19Z  2018-12-18T07:44:19Z   
83147  UC-z1ubmS-iHMVr83EEwRS2g  2018-12-14T17:38:59Z  2018-12-14T17:38:59Z   
5076   UC-z1ubmS-iHMVr83EEwRS2g  2020-12-29T14:40:24Z  2021-09-11T20:17:04Z   
3628   UC-z1ubmS-iHMVr83EEwRS2g  2021-01-02T15:23:08Z  2021-01-02T15:23:08Z   

       likeCount                                        textDisplay  \
5829       28917  Jumlah orang yg habis nonton yt reward 2020 te...   
87787      27096                         Hidup YouTubers Indonesia!   
85205      11247                              Kisses from France ♥️   
14938      10998  Hapus aja deh biar yg lain penasaran wkwk<br><...   
6340        9036                            Menantikan Rewind 2020🔥   
20725       8369  List Lagu Youtube Rewind INDONESIA 2018 :\r<br...   
29089       7582  DAFTAR LAGU YTR INDO 2018<br><br><a href="http...   
83147       5274           Congrats buat semua Tim yang bertugas :)   
5076        5261  Gausah dibandingin sih semuanya bagus, udah gi...   
3628        4999                  gua kangen suasana tanpa masker:(   

                                            textOriginal viewerRating  \
5829   Jumlah orang yg habis nonton yt reward 2020 te...         none   
87787                         Hidup YouTubers Indonesia!         none   
85205                              Kisses from France ♥️         none   
14938  Hapus aja deh biar yg lain penasaran wkwk\n\nE...         none   
6340                             Menantikan Rewind 2020🔥         none   
20725  List Lagu Youtube Rewind INDONESIA 2018 :\r\n\...         none   
29089  DAFTAR LAGU YTR INDO 2018\n\n0:05 = Post Malon...         none   
83147           Congrats buat semua Tim yang bertugas :)         none   
5076   Gausah dibandingin sih semuanya b

Migrasi dari MongoDB Local ke MongoDB Atlas

In [4]:
# Koneksi ke MongoDB lokal
local_client = MongoClient(local_url)
local_db = local_client[database_name]
local_collection = local_db[collection_name]

# Koneksi ke MongoDB Atlas
atlas_client = MongoClient(mongodb_url)
atlas_db = atlas_client[database_name]
atlas_collection = atlas_db[collection_name]

# Ambil semua dokumen dari koleksi MongoDB lokal
documents = list(local_collection.find())

# Masukkan dokumen ke MongoDB Atlas
if documents:
    atlas_collection.insert_many(documents)
    print(f'{len(documents)} dokumen berhasil dipindahkan dari MongoDB lokal ke MongoDB Atlas.')
else:
    print('Tidak ada dokumen yang ditemukan di MongoDB lokal.')

# Tutup koneksi
local_client.close()
atlas_client.close()

111464 dokumen berhasil dipindahkan dari MongoDB lokal ke MongoDB Atlas.
